In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
# from bs4 import BeautifulSoup
import requests
from urllib.request import urlopen
from sklearn.preprocessing import MinMaxScaler


import seaborn as sns

%matplotlib inline

In [2]:
df = pd.read_csv('../input/2012_qb_weeks1_8.csv')
df1=pd.read_csv('../input/2012_qb_weeks_9_16.csv')
df3 = pd.read_csv('../input/2012_qb_week17.csv')

In [3]:
raw_qb_2012 = pd.concat([df,df1], axis=0)
raw_qb_2012 = pd.concat([raw_qb_2012, df3], axis=0)
raw_qb_2012.drop('Rk', axis =1, inplace = True)
raw_qb_2012.shape

(629, 18)

In [4]:
raw_qb_2012.head()

Player Pos  Week Team  Opp  Comp  Att  Pct  Yds  Yds/Att  TD  \
0           Matt Ryan  QB     1  ATL   KC    23   31   74  299       10   3   
1  Robert Griffin III  QB     1  WAS   NO    19   26   73  320       12   2   
2           Tony Romo  QB     1  DAL  NYG    22   29   76  307       11   3   
3       Aaron Rodgers  QB     1   GB   SF    30   44   68  303        7   2   
4          Drew Brees  QB     1   NO  WAS    24   52   46  339        7   3   

   Int  QB Rating  Att.1  Yds.1  Yds/Att.1  TD.1  Fantasy Points  
0    0        136      3     25          8     1           32.46  
1    0        140      9     42          5     0           25.00  
2    1        130      5     12          2     0           23.48  
3    1         93      5     27          5     0           22.82  
4    2         71      0      0          0     0           21.56

In [5]:
raw_qb_2012 = raw_qb_2012.rename(columns={'Att.1':'rush_att',
                       'Yds.1':'rush_yds',
                       'Yds/Att.1':'rush_yd/att',
                       'TD.1':'rush_td'})

In [6]:
team_stats = raw_qb_2012.groupby(['Player','Week','Opp']).sum()

In [7]:
team_stats.head(), team_stats.shape

(                        Comp  Att  Pct  Yds  Yds/Att  TD  Int  QB Rating  \
 Player        Week Opp                                                     
 Aaron Rodgers 1    SF     30   44   68  303        7   2    1         93   
               2    CHI    22   32   69  219        7   1    1         85   
               3    SEA    26   39   67  223        6   0    0         81   
               4    NO     31   41   76  319        8   4    1        120   
               5    IND    20   32   63  235        7   3    1        103   
 
                         rush_att  rush_yds  rush_yd/att  rush_td  \
 Player        Week Opp                                             
 Aaron Rodgers 1    SF          5        27            5        0   
               2    CHI         3        -6           -2        0   
               3    SEA         2        17            9        0   
               4    NO          5        13            3        0   
               5    IND         5        57  

In [8]:
y=team_stats['Fantasy Points']

In [9]:
team_stats.drop('Fantasy Points', axis =1, inplace = True)

In [10]:
# Define a dataframe to contain the current year averages of all 2012 QBs
def create_current_dataframe(df):
    columns = []
    for col in df.columns:
        columns.append('avg_{}'.format(col.lower()))
    new_df = pd.DataFrame(columns=columns, index =df.index)
    return new_df

In [11]:
qb_current_2012 = create_current_dataframe(team_stats)

In [12]:
# Populate current dataframe with current year averages of players
# DO NOT CHANGE!!!!!!
for col in team_stats:  # Iterate through every attribute in the team_stats dataframe
    points=[]  # Create an empty list to hold the season average of the current attribute
    for player in team_stats.index.levels[0]:  # Iterate through every player in the team_stats df
        total =[] # create an empty list to hold the weekly attributes value
        for week in team_stats.loc[player].index: # Iterate throough every week for the current player
            total.append(team_stats.loc[player].loc[week][col]) # Add player's value for the current week's attribute to the total list
            points.append(np.mean(total))  # Add the average of the total list to the season average list
    qb_current_2012['avg_{}'.format(col.lower())] = points # Insert season average list for current attribute into the current stats dataframe
    

In [13]:
qb_current_2012[0:30]

avg_comp    avg_att    avg_pct     avg_yds  \
Player        Week Opp                                                
Aaron Rodgers 1    SF   30.000000  44.000000  68.000000  303.000000   
              2    CHI  26.000000  38.000000  68.500000  261.000000   
              3    SEA  26.000000  38.333333  68.000000  248.333333   
              4    NO   27.250000  39.000000  70.000000  266.000000   
              5    IND  25.800000  37.600000  68.600000  259.800000   
              6    HOU  25.500000  37.500000  68.000000  272.833333   
              7    LAR  26.142857  37.428571  69.857143  282.714286   
              8    JAX  25.625000  37.125000  69.000000  270.625000   
              9    ARI  24.333333  36.333333  66.555556  264.777778   
              11   DET  23.800000  35.400000  66.900000  261.900000   
              12   NYG  22.909091  34.454545  65.909091  258.000000   
              13   MIN  23.250000  34.500000  66.833333  260.333333   
              14   DET  22.538462  33.692308  66.153846  253.615385   
              15   CHI  22.571429  33.857143  66.000000  256.285714   
              16   TEN  22.866667  34.133333  66.333333  262.000000   
              17   MIN  23.187500  34.500000  66.562500  268.437500   
Alex Smith    1    GB   20.000000  26.000000  77.000000  211.000000   
              2    DET  20.000000  28.500000  71.000000  218.500000   
              3    MIN  21.333333  30.666667  70.333333  213.666667   
              4    NYJ  19.000000  28.250000  67.000000  196.000000   
              5    BUF  18.800000  27.400000  68.600000  217.400000   
              6    NYG  18.833333  27.833333  67.666667  214.500000   
              7    SEA  18.142857  27.142857  66.714286  203.857143   
              8    ARI  18.125000  26.125000  70.250000  207.375000   
              10   LAR  16.888889  24.111111  72.222222  192.333333   
              11   CHI  15.200000  21.700000  65.000000  173.100000   
              12   NO   13.818182  19.727273  59.090909  157.363636   
              13   LAR  12.666667  18.083333  54.166667  144.250000   
              14   MIA  11.692308  16.692308  50.000000  133.153846   
              15   NE   10.857143  15.500000  46.428571  123.642857   

                        avg_yds/att    avg_td   avg_int  avg_qb rating  \
Player        Week Opp                                                   
Aaron Rodgers 1    SF      7.000000  2.000000  1.000000      93.000000   
              2    CHI     7.000000  1.500000  1.000000      89.000000   
              3    SEA     6.666667  1.000000  0.666667      86.333333   
              4    NO      7.000000  1.750000  0.750000      94.750000   
              5    IND     7.000000  2.000000  0.800000      96.400000   
              6    HOU     7.333333  2.666667  0.666667     102.666667   
              7    LAR     7.571429  2.714286  0.571429     106.857143   
              8    JAX     7.250000  2.625000  0.500000     105.500000   
              9    ARI     7.222222  2.777778  0.555556     104.555556   
              11   DET     7.400000  2.700000  0.600000     104.700000   
              12   NYG     7.545455  2.545455  0.636364     102.636364   
              13   MIN     7.583333  2.416667  0.666667     102.250000   
              14   DET     7.538462  2.230769  0.615385     100.615385   
              15   CHI     7.571429  2.285714  0.571429     101.785714   
              16   TEN     7.666667  2.333333  0.533333     103.333333   
              17   MIN     7.750000  2.437500  0.500000     105.125000   
Alex Smith    1    GB      8.000000  2.000000  0.000000     126.000000   
              2    DET     7.500000  2.000000  0.000000     117.000000   
              3    MIN     7.000000  1.666667  0.333333     105.000000   
              4    NYJ     7.000000  1.250000  0.250000      98.250000   
              5    BUF     8.200000  1.600000  0.200000     109.800000   
              6    NYG     8.000000  1.333333  0.6

In [14]:
#A function that will covert a time series database into a supervised learning database

def series_to_supervised(data, n_in=1, n_out=1, dropnan=True):
    n_vars = 1 if type(data) is list else data.shape[1]
    df = pd.DataFrame(data)
    cols, names = list(), list()
    # input sequence (t-n, ... t-1)
    for i in range(n_in, 0, -1):
            cols.append(df.shift(i))
            names += [('var%d(t-%d)' % (j+1, i)) for j in range(n_vars)]
    # forecast sequence (t, t+1, ... t+n)
    for i in range(0, n_out):
        cols.append(df.shift(-i))
        if i == 0:
            names += [('var%d(t)' % (j+1)) for j in range(n_vars)]
        else:
            names += [('var%d(t+%d)' % (j+1, i)) for j in range(n_vars)]
    # put it all together
    agg = pd.concat(cols, axis=1)
    agg.columns = names
    # drop rows with NaN values
    if dropnan:
        agg.dropna(inplace=True)
    return agg

In [15]:
df= qb_current_2012.astype('float32')



# scale data, reframe for supervised learning and drop target variable
scaler = MinMaxScaler(feature_range=(0,1))
scaled  = scaler.fit_transform(df)
reframed = series_to_supervised(scaled, 1, 1)
reframed.head()


var1(t-1)  var2(t-1)  var3(t-1)  var4(t-1)  var5(t-1)  var6(t-1)  \
1   0.937500   0.785714      0.680   0.838174   0.350000   0.666667   
2   0.812500   0.678571      0.685   0.721992   0.350000   0.500000   
3   0.812500   0.684524      0.680   0.686952   0.333333   0.333333   
4   0.851562   0.696429      0.700   0.735823   0.350000   0.583333   
5   0.806250   0.671429      0.686   0.718672   0.350000   0.666667   

   var7(t-1)  var8(t-1)  var9(t-1)  var10(t-1)    ...     var3(t)   var4(t)  \
1   0.250000   0.588608   0.454545    0.437500    ...       0.685  0.721992   
2   0.250000   0.563291   0.363636    0.204637    ...       0.680  0.686952   
3   0.166667   0.546414   0.303030    0.235215    ...       0.700  0.735823   
4   0.187500   0.599684   0.340909    0.236391    ...       0.686  0.718672   
5   0.200000   0.610127   0.363636    0.361290    ...       0.680  0.754726   

    var5(t)   var6(t)   var7(t)   var8(t)   var9(t)  var10(t)  var11(t)  \
1  0.350000  0.500000  0.250000  0.563291  0.363636  0.204637  0.184211   
2  0.333333  0.333333  0.166667  0.546414  0.303030  0.235215  0.315789   
3  0.350000  0.583333  0.187500  0.599684  0.340909  0.236391  0.302632   
4  0.350000  0.666667  0.200000  0.610127  0.363636  0.361290  0.378947   
5  0.366667  0.888889  0.166667  0.649789  0.333333  0.350470  0.412281   

   var12(t)  
1       0.0  
2       0.0  
3       0.0  
4       0.0  
5       0.0  

[5 rows x 24 columns]

In [16]:
reframed[0:30]

var1(t-1)  var2(t-1)  var3(t-1)  var4(t-1)  var5(t-1)  var6(t-1)  \
1    0.937500   0.785714   0.680000   0.838174   0.350000   0.666667   
2    0.812500   0.678571   0.685000   0.721992   0.350000   0.500000   
3    0.812500   0.684524   0.680000   0.686952   0.333333   0.333333   
4    0.851562   0.696429   0.700000   0.735823   0.350000   0.583333   
5    0.806250   0.671429   0.686000   0.718672   0.350000   0.666667   
6    0.796875   0.669643   0.680000   0.754726   0.366667   0.888889   
7    0.816964   0.668367   0.698571   0.782059   0.378571   0.904762   
8    0.800781   0.662946   0.690000   0.748617   0.362500   0.875000   
9    0.760417   0.648810   0.665556   0.732442   0.361111   0.925926   
10   0.743750   0.632143   0.669000   0.724481   0.370000   0.900000   
11   0.715909   0.615260   0.659091   0.713693   0.377273   0.848485   
12   0.726562   0.616071   0.668333   0.720148   0.379167   0.805556   
13   0.704327   0.601648   0.661538   0.701564   0.376923   0.743590   
14   0.705357   0.604592   0.660000   0.708951   0.378571   0.761905   
15   0.714583   0.609524   0.663333   0.724758   0.383333   0.777778   
16   0.724609   0.616071   0.665625   0.742566   0.387500   0.812500   
17   0.625000   0.464286   0.770000   0.583679   0.400000   0.666667   
18   0.625000   0.508929   0.710000   0.604426   0.375000   0.666667   
19   0.666667   0.547619   0.703333   0.591056   0.350000   0.555556   
20   0.593750   0.504464   0.670000   0.542185   0.350000   0.416667   
21   0.587500   0.489286   0.686000   0.601383   0.410000   0.533333   
22   0.588542   0.497024   0.676667   0.593361   0.400000   0.444444   
23   0.566964   0.484694   0.667143   0.563920   0.385714   0.428571   
24   0.566406   0.466518   0.702500   0.573651   0.412500   0.500000   
25   0.527778   0.430556   0.722222   0.532042   0.416667   0.481481   
26   0.475000   0.387500   0.650000   0.478838   0.375000   0.433333   
27   0.431818   0.352273   0.590909   0.435307   0.340909   0.393939   
28   0.395833   0.322917   0.541667   0.399032   0.312500   0.361111   
29   0.365385   0.298077   0.500000   0.368337   0.288462   0.333333   
30   0.339286   0.276786   0.464286   0.342027   0.267857   0.309524   

    var7(t-1)  var8(t-1)  var9(t-1)  var10(t-1)    ...      var3(t)   var4(t)  \
1    0.250000   0.588608   0.454545    0.437500    ...     0.685000  0.721992   
2    0.250000   0.563291   0.363636    0.204637    ...     0.680000  0.686952   
3    0.166667   0.546414   0.303030    0.235215    ...     0.700000  0.735823   
4    0.187500   0.599684   0.340909    0.236391    ...     0.686000  0.718672   
5    0.200000   0.610127   0.363636    0.361290    ...     0.680000  0.754726   
6    0.166667   0.649789   0.333333    0.350470    ...     0.698571  0.782059   
7    0.142857   0.676311   0.311688    0.308468    ...     0.690000  0.748617   
8    0.125000   0.667722   0.306818    0.284022    ...     0.665556  0.732442   
9    0.138889   0.661744   0.353535    0.310484    ...     0.669000  0.724481   
10   0.150000   0.662658   0.327273    0.289315    ...     0.659091  0.713693   
11   0.159091   0.649597   0.322314    0.296371    ...     0.668333  0.720148   
12   0.166667   0.647152   0.325758    0.294019    ...     0.661538  0.701564   
13   0.153846   0.636806   0.321678    0.310484    ...     0.660000  0.708951   
14   0.142857   0.644213   0.324675    0.306452    ...     0.663333  0.724758   
15   0.133333   0.654008   0.327273    0.300134    ...     0.665625  0.742566   
16   0.125000   0.665348   0.306818    0.284904    ...     0.770000  0.583679   
17   0.000000   0.797468   0.454545    0.239919    ...     0.710000  0.604426   
18   0.000000   0.740506   0.409091    0.197581    ...     0.703333  0.591056   
19   0.083333   0.664557   0.393939    0.272849    ...     0.670000  0.542185   
20   0.062500   0.621835   0.363636    0.261089    ...     0.686000  0.601383   
21   0.050000   0.694937   0.345455    0.358468    ...     0.676667  0

In [17]:
qb_current_2012.shape[1]

12

In [18]:
X=reframed.values

In [19]:
y=y[1:]


In [20]:
from sklearn.linear_model import LinearRegression
lr = LinearRegression()
lr.fit(X, y)

LinearRegression(copy_X=True, fit_intercept=True, n_jobs=1, normalize=False)

In [21]:
yhat=lr.predict(X)
yhat

array([  1.00928393e+01,   1.25007244e+01,   2.09211882e+01,
         2.08519861e+01,   2.53981537e+01,   2.16773523e+01,
         1.95419706e+01,   2.13170426e+01,   1.95604171e+01,
         1.87278243e+01,   1.83724753e+01,   1.85434509e+01,
         1.95131741e+01,   2.05550976e+01,   2.10943784e+01,
         1.17355515e+01,   1.69438885e+01,   1.41798100e+01,
         1.18736283e+01,   2.02080843e+01,   1.19015208e+01,
         1.27840775e+01,   1.58620908e+01,   1.29625729e+01,
         1.20784207e+01,   1.10391462e+01,   1.01680782e+01,
         9.42755028e+00,   8.79033979e+00,   8.23627472e+00,
         7.55025030e+00,   5.01845336e+00,   2.04491285e+01,
         2.03273086e+01,   2.08656789e+01,   1.40369586e+01,
         1.79420454e+01,   1.72243546e+01,   1.93210163e+01,
         1.81620604e+01,   1.75792688e+01,   1.70581592e+01,
         1.91771419e+01,   1.65328824e+01,   1.73137716e+01,
         1.66965003e+01,   1.66984220e+01,  -1.16113932e+00,
         2.38846334e+01,

In [22]:
yhat.shape, y.shape

((628,), (628,))

In [ ]:
for valh in yhat:
    for val in y:
        print(np.mean(valh.astype('float64')-val.astype('float64')))

-0.0671607333156
-0.527160733316
-17.9671607333
-15.0071607333
-29.1271607333
-15.5871607333
-3.74716073332
-15.9271607333
-5.64716073332
-0.867160733316
-4.84716073332
-4.02716073332
-15.8471607333
-22.6871607333
-18.5071607333
-7.64716073332
-7.64716073332
-0.667160733316
3.17283926668
-18.9271607333
7.59283926668
1.39283926668
-11.7871607333
2.71283926668
10.0928392667
10.0928392667
10.0928392667
10.0928392667
10.0928392667
10.0928392667
10.0528392667
0.832839266684
-8.96716073332
-13.4271607333
-18.7871607333
4.99283926668
-8.54716073332
-6.58716073332
-15.7271607333
-8.08716073332
-3.66716073332
-3.50716073332
-18.8471607333
1.55283926668
-6.34716073332
-4.20716073332
-5.64716073332
4.15283926668
-13.0271607333
-14.6271607333
-12.1671607333
-1.36716073332
-9.64716073332
3.99283926668
-5.46716073332
-13.6671607333
-14.4071607333
-10.8071607333
-4.84716073332
-0.147160733316
-2.78716073332
2.97283926668
2.57283926668
-6.10716073332
-8.90716073332
-22.0671607333
-4.10716073332
-7.827

16.1611882256
6.8811882256
-11.0188117744
13.2211882256
6.1211882256
0.501188225595
13.3811882256
-0.278811774405
-4.4988117744
-3.4588117744
-1.1388117744
-3.6788117744
1.4811882256
6.4811882256
0.121188225595
3.4211882256
1.7411882256
6.8211882256
8.7611882256
-2.6388117744
-3.2388117744
7.8811882256
-1.3388117744
17.8011882256
6.5611882256
2.7611882256
15.2811882256
14.7611882256
6.3211882256
-1.0588117744
8.6011882256
7.8011882256
11.7211882256
0.621188225595
15.6811882256
5.9211882256
7.1811882256
-4.0788117744
-9.5188117744
-3.3188117744
-1.5988117744
16.5811882256
-14.1588117744
-2.2988117744
9.0411882256
7.0211882256
-11.4788117744
-8.1388117744
3.2011882256
3.8411882256
6.6011882256
4.6211882256
12.8011882256
8.0811882256
5.9211882256
19.1211882256
10.8811882256
-2.4988117744
17.0411882256
4.5811882256
-0.698811774405
4.0011882256
0.161188225595
-5.8988117744
11.8011882256
-18.4788117744
-2.8188117744
-4.8788117744
19.5611882256
6.3211882256
2.4011882256
1.6011882256
-2.478811

13.9570426107
22.3570426107
20.0370426107
17.0170426107
21.4770426107
16.8170426107
18.3770426107
4.07704261074
16.5570426107
17.8770426107
17.7370426107
18.9570426107
22.0970426107
-0.16295738926
11.8370426107
10.5170426107
5.47704261074
5.77704261074
2.35704261074
15.7570426107
17.1770426107
6.91704261074
12.1970426107
5.65704261074
11.1370426107
10.6570426107
16.7570426107
19.1170426107
9.71704261074
21.4170426107
21.4170426107
21.7170426107
21.4170426107
21.4370426107
21.3170426107
18.9170426107
18.3970426107
6.25704261074
8.79704261074
-3.90295738926
11.0370426107
-9.88295738926
13.4770426107
4.99704261074
9.05704261074
-0.42295738926
6.97704261074
3.23704261074
-16.1229573893
-7.76295738926
-15.7629573893
3.37704261074
0.51704261074
9.99704261074
3.43704261074
3.69704261074
2.45704261074
13.2370426107
7.19704261074
1.99704261074
7.05704261074
-7.54295738926
2.59704261074
4.63704261074
15.4770426107
0.97704261074
6.49704261074
13.6370426107
20.0770426107
22.3970426107
18.077042610

14.4034509375
4.14345093752
9.42345093752
2.88345093752
8.36345093752
7.88345093752
13.9834509375
16.3434509375
6.94345093752
18.6434509375
18.6434509375
18.9434509375
18.6434509375
18.6634509375
18.5434509375
16.1434509375
15.6234509375
3.48345093752
6.02345093752
-6.67654906248
8.26345093752
-12.6565490625
10.7034509375
2.22345093752
6.28345093752
-3.19654906248
4.20345093752
0.463450937522
-18.8965490625
-10.5365490625
-18.5365490625
0.603450937522
-2.25654906248
7.22345093752
0.663450937522
0.923450937522
-0.316549062478
10.4634509375
4.42345093752
-0.776549062478
4.28345093752
-10.3165490625
-0.176549062478
1.86345093752
12.7034509375
-1.79654906248
3.72345093752
10.8634509375
17.3034509375
19.6234509375
15.3034509375
11.7034509375
-12.3165490625
2.10345093752
3.96345093752
15.0434509375
8.10345093752
4.42345093752
3.32345093752
16.5834509375
5.50345093752
18.5434509375
18.5434509375
18.5434509375
18.5434509375
18.5434509375
18.5434509375
18.5434509375
18.5434509375
18.5434509375


6.63555153128
-6.90444846872
-4.94444846872
-14.0844484687
-6.44444846872
-2.02444846872
-1.86444846872
-17.2044484687
3.19555153128
-4.70444846872
-2.56444846872
-4.00444846872
5.79555153128
-11.3844484687
-12.9844484687
-10.5244484687
0.275551531278
-8.00444846872
5.63555153128
-3.82444846872
-12.0244484687
-12.7644484687
-9.16444846872
-3.20444846872
1.49555153128
-1.14444846872
4.61555153128
4.21555153128
-4.46444846872
-7.26444846872
-20.4244484687
-2.46444846872
-6.18444846872
-1.28444846872
-9.74444846872
-0.804448468722
2.97555153128
-10.7644484687
-8.02444846872
2.63555153128
-5.42444846872
-7.26444846872
5.11555153128
0.435551531278
0.395551531278
11.9555515313
3.33555153128
-4.38444846872
-3.46444846872
4.37555153128
12.7755515313
10.4555515313
7.43555153128
11.8955515313
7.23555153128
8.79555153128
-5.50444846872
6.97555153128
8.29555153128
8.15555153128
9.37555153128
12.5155515313
-9.74444846872
2.25555153128
0.935551531278
-4.10444846872
-3.80444846872
-7.22444846872
6.17

...

-14.0690160371
-2.94901603708
-12.1690160371
6.97098396292
-4.26901603708
-8.06901603708
4.45098396292
3.93098396292
-4.50901603708
-11.8890160371
-2.22901603708
-3.02901603708
0.890983962917
-10.2090160371
4.85098396292
-4.90901603708
-3.64901603708
-14.9090160371
-20.3490160371
-14.1490160371
-12.4290160371
5.75098396292
-24.9890160371
-13.1290160371
-1.78901603708
-3.80901603708
-22.3090160371
-18.9690160371
-7.62901603708
-6.98901603708
-4.22901603708
-6.20901603708
1.97098396292
-2.74901603708
-4.90901603708
8.29098396292
0.0509839629172
-13.3290160371
6.21098396292
-6.24901603708
-11.5290160371
-6.82901603708
-10.6690160371
-16.7290160371
0.970983962917
-29.3090160371
-13.6490160371
-15.7090160371
8.73098396292
-4.50901603708
-8.42901603708
-9.22901603708
-13.3090160371
6.95098396292
3.47098396292
-9.20901603708
1.13098396292
-8.58901603708
1.87098396292
-0.309016037083
-8.18901603708
-2.28901603708
2.61098396292
-1.30901603708
-2.90901603708
9.53098396292
5.51098396292
9.2109839

-2.38164612607
-6.22164612607
-12.2816461261
5.41835387393
-24.8616461261
-9.20164612607
-11.2616461261
13.1783538739
-0.0616461260653
-3.98164612607
-4.78164612607
-8.86164612607
11.3983538739
7.91835387393
-4.76164612607
5.57835387393
-4.14164612607
6.31835387393
4.13835387393
-3.74164612607
2.15835387393
7.05835387393
3.13835387393
1.53835387393
13.9783538739
9.95835387393
13.6583538739
14.3783538739
11.5783538739
10.8983538739
14.1583538739
14.5383538739
14.8383538739
16.8383538739
12.1783538739
-4.86164612607
8.39835387393
-2.70164612607
6.01835387393
-2.46164612607
13.8183538739
-0.961646126065
11.9583538739
8.19835387393
-0.881646126065
1.19835387393
2.03835387393
-7.46164612607
-3.06164612607
8.33835387393
2.41835387393
-8.86164612607
11.0583538739
7.89835387393
2.89835387393
-9.46164612607
2.33835387393
4.03835387393
-4.46164612607
3.03835387393
0.238353873935
0.598353873935
0.878353873935
-13.4416461261
0.798353873935
1.85835387393
-0.241646126065
14.5383538739
15.6183538739


-0.372916356634
0.267083643366
3.02708364337
1.04708364337
9.22708364337
4.50708364337
2.34708364337
15.5470836434
7.30708364337
-6.07291635663
13.4670836434
1.00708364337
-4.27291635663
0.427083643366
-3.41291635663
-9.47291635663
8.22708364337
-22.0529163566
-6.39291635663
-8.45291635663
15.9870836434
2.74708364337
-1.17291635663
-1.97291635663
-6.05291635663
14.2070836434
10.7270836434
-1.95291635663
8.38708364337
-1.33291635663
9.12708364337
6.94708364337
-0.932916356634
4.96708364337
9.86708364337
5.94708364337
4.34708364337
16.7870836434
12.7670836434
16.4670836434
17.1870836434
14.3870836434
13.7070836434
16.9670836434
17.3470836434
17.6470836434
19.6470836434
14.9870836434
-2.05291635663
11.2070836434
0.107083643366
8.82708364337
0.347083643366
16.6270836434
1.84708364337
14.7670836434
11.0070836434
1.92708364337
4.00708364337
4.84708364337
-4.65291635663
-0.252916356634
11.1470836434
5.22708364337
-6.05291635663
13.8670836434
10.7070836434
5.70708364337
-6.65291635663
5.147083

-7.82557157772
-6.10557157772
12.0744284223
-18.6655715777
-6.80557157772
4.53442842228
2.51442842228
-15.9855715777
-12.6455715777
-1.30557157772
-0.665571577721
2.09442842228
0.114428422279
8.29442842228
3.57442842228
1.41442842228
14.6144284223
6.37442842228
-7.00557157772
12.5344284223
0.0744284222792
-5.20557157772
-0.505571577721
-4.34557157772
-10.4055715777
7.29442842228
-22.9855715777
-7.32557157772
-9.38557157772
15.0544284223
1.81442842228
-2.10557157772
-2.90557157772
-6.98557157772
13.2744284223
9.79442842228
-2.88557157772
7.45442842228
-2.26557157772
8.19442842228
6.01442842228
-1.86557157772
4.03442842228
8.93442842228
5.01442842228
3.41442842228
15.8544284223
11.8344284223
15.5344284223
16.2544284223
13.4544284223
12.7744284223
16.0344284223
16.4144284223
16.7144284223
18.7144284223
14.0544284223
-2.98557157772
10.2744284223
-0.825571577721
7.89442842228
-0.585571577721
15.6944284223
0.914428422279
13.8344284223
10.0744284223
0.994428422279
3.07442842228
3.91442842228


8.32370802102
-2.91629197898
-6.71629197898
5.80370802102
5.28370802102
-3.15629197898
-10.536291979
-0.876291978976
-1.67629197898
2.24370802102
-8.85629197898
6.20370802102
-3.55629197898
-2.29629197898
-13.556291979
-18.996291979
-12.796291979
-11.076291979
7.10370802102
-23.636291979
-11.776291979
-0.436291978976
-2.45629197898
-20.956291979
-17.616291979
-6.27629197898
-5.63629197898
-2.87629197898
-4.85629197898
3.32370802102
-1.39629197898
-3.55629197898
9.64370802102
1.40370802102
-11.976291979
7.56370802102
-4.89629197898
-10.176291979
-5.47629197898
-9.31629197898
-15.376291979
2.32370802102
-27.956291979
-12.296291979
-14.356291979
10.083708021
-3.15629197898
-7.07629197898
-7.87629197898
-11.956291979
8.30370802102
4.82370802102
-7.85629197898
2.48370802102
-7.23629197898
3.22370802102
1.04370802102
-6.83629197898
-0.936291978976
3.96370802102
0.0437080210237
-1.55629197898
10.883708021
6.86370802102
10.563708021
11.283708021
8.48370802102
7.80370802102
11.063708021
11.4437